In [68]:
import dtvf
import numpy as np
import pandas as pd

#def main():
optimizer=dtvf.DTVFOptimizerByGA(ts = 0.001)
population = optimizer.init_population(size = 100)

#load sample data 1
df = pd.read_csv('data/sample.csv')
df = df.iloc[:,1:]

In [3]:
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

init_notebook_mode()

params={'f_o': 850.0500808025597,
 'f_inf': 0.006954969169234533,
 'k': 2,
 'n_alpha': 61.213235806445226,
 'alpha': 0.018375634371429625
       }

flt=dtvf.DiscTimeVarFilt(ts = 0.001,**params)
y_1 = flt.apply_filter(df,xs=0, ys=0)



traces = []
for idx in range(0, y_1.shape[1]):
    traces.append(go.Scatter(y = y_1[:, idx],
                            mode = 'lines',
                            name = 'wvf'+str(idx+1)
                            )
                 )

iplot(traces)

In [5]:
#load cv data 2
df_cv = pd.read_csv('data/sample-cv.csv')
df_cv = df_cv.iloc[:,1:]

flt=dtvf.DiscTimeVarFilt(ts = 0.001,**params)
y_cv = flt.apply_filter(df_cv,xs=0, ys=0)

traces = []
for idx in range(0, y_cv.shape[1]):
    traces.append(go.Scatter(y = y_cv[:, idx],
                            mode = 'lines',
                            name = 'wvf'+str(idx+1),
                             text = "cross-validation data"
                            )
                 )

iplot(traces)

In [16]:
print([y_1[99,:].std()*3, y_1[99,:].mean()-22.51])
print([y_cv[99,:].std()*3, y_cv[99,:].mean()-22.51])

[0.1902619057174998, -0.4182551965414518]
[0.2033340784458208, -0.3911104364939213]


In [8]:
import numpy as np
import matplotlib.pyplot as plt

tx=np.arange(0,1,0.01)
ty=np.arange(-0.5,0.5,0.001)

sx=0.4
sy=0.3

x,y = np.meshgrid(tx,ty,sparse=True)
gauss=100*np.exp(-1*((x**2/(2*sx**2))+(y**2/(2*sy**2))))
plt.contourf(tx,ty,gauss)
plt.show()

<Figure size 640x480 with 1 Axes>

In [13]:
# For fir filter comparison hamming

import ffa

fir_filter = ffa.FIRFilterA(taps = 17,
                            f_c = 1,
                            f_s = 1000,
                            filter_type = "low", window = "hamm")
# plot using plotly
#load cv data 2

flt_hamm = ffa.FIRFilterA(taps = 17,
                            f_c = 1,
                            f_s = 1000,
                            filter_type = "low", window = "hamm")
y_hamm = flt_hamm.apply_filter(np.asarray(df))
y_hamm_cv = flt_hamm.apply_filter(np.asarray(df_cv))

traces = []
for idx in range(0, y_hamm.shape[1]):
    traces.append(go.Scatter(y = y_hamm[:, idx],
                            mode = 'lines',
                            name = 'wvf'+str(idx+1),
                             text = "sample data"
                            )
                 )
traces_cv = []
for idx in range(0, y_hamm_cv.shape[1]):
    traces_cv.append(go.Scatter(y = y_hamm_cv[:, idx],
                            mode = 'lines',
                            name = 'wvf'+str(idx+1),
                             text = "cross-validation data"
                            )
                 )

iplot(traces)
iplot(traces_cv)

In [15]:
print([y_hamm[99,:].std()*3, y_hamm[99,:].mean()-22.51])
print([y_hamm_cv[99,:].std()*3, y_hamm_cv[99,:].mean()-22.51])

[1.0287671309473247, 0.07508843939735854]
[1.2961592421193673, 0.17110453621956268]


In [29]:
wc=flt.wc_fxn(range(400))/(2*np.pi)
trace_wc = go.Scatter(y = wc,
                     mode = 'lines',
                     name = 'f(n)'
                     )
layout_wc = go.Layout(title = "time-varying cutoff frequency",
                    xaxis= dict(title = 'samples (n)'),
                    yaxis= dict(title = 'frequency (Hz)')
                    )
iplot(go.Figure(data=[trace_wc],layout = layout_wc))

In [67]:
import os
import csv
import numpy as np
import ffa
import dtvf

f_s=1000
meas_time = 99 # T1+T2
real_val_bt = 22.51 # 22.51g for BT workpiece
real_val_ideal = 26.53 # 26.53g for ideal workpiece

#design hamming filter
flt_hamm = ffa.FIRFilterA(taps = 17,
                            f_c = 1,
                            f_s = f_s,
                            filter_type = "low", window = "hamm")
#design hanning filter
flt_hann = ffa.FIRFilterA(taps = 17,
                            f_c = 1,
                            f_s = f_s,
                            filter_type = "low", window = "hann")

#design discrete time-varying filter with params given
params={'f_o': 850.0500808025597,
         'f_inf': 0.006954969169234533,
         'k': 2,
         'n_alpha': 61.213235806445226,
         'alpha': 0.018375634371429625
               }

flt_dtvf = dtvf.DiscTimeVarFilt(ts = 1/f_s,**params)
  
# apply to test data
path = 'data/testdata_bt'

# r=root, d=directories, f = files
for r, d, f in os.walk(path):
    metrics = np.zeros((len(f), 6))
    for idx,file in enumerate(f):
        if '.csv' in file:
            file_link = os.path.join(r, file)
            df_walk = pd.read_csv(file_link).iloc[:,1:]
            x = np.asarray(df_walk)
            y_hamm = flt_hamm.apply_filter(x)
            y_hann = flt_hann.apply_filter(x)
            y_dtvf = flt_dtvf.apply_filter(x, xs=0, ys=0)
            std3 = np.array([y_hamm[meas_time, :].std()*3, y_hann[meas_time, :].std()*3, y_dtvf[meas_time, :].std()*3])
            xbar_x = np.array([y_hamm[meas_time, :].mean()-real_val_bt, y_hann[meas_time, :].mean()-real_val_bt, y_dtvf[meas_time, :].mean()-real_val_bt])
            metrics[idx, :] = np.concatenate((std3, xbar_x))
            print("file '",file,"': ",[std3, xbar_x])

names = ["hamming", "hanning", "DTVF"]
traces_3s = []
traces_xbarx = []
for idx in range(3):
    traces_3s.append(go.Bar(
                    x = ["no. "+ str(i) for i in range(metrics.shape[0])],
                    y = metrics[:, idx],
                    name = names[idx]
                )
    )
    traces_xbarx.append(go.Bar(
                    x = ["no. "+ str(i) for i in range(metrics.shape[0])],
                    y = metrics[:, 3 + idx],
                    name = names[idx]
                )
    )

data = traces
layout_3s = go.Layout(
    barmode='group',
    xaxis= dict(title = 'test data '),
    yaxis= dict(title = 'Accuracy 3s (grams)')
) 
layout_xbarx = go.Layout(
    barmode='group',
    xaxis= dict(title = 'test data '),
    yaxis= dict(title = 'Xbar-x (grams)')
) 

fig_3s = go.Figure(data=traces_3s, layout=layout_xbarx)
iplot(fig_3s, filename='grouped-bar')
fig_xbarx = go.Figure(data=traces_xbarx, layout=layout_xbarx)
iplot(fig_xbarx, filename='grouped-bar')

file ' ダイナミックBT2_現行PIDq.csv ':  [array([1.20934228, 1.78605762, 0.44915935]), array([-0.08561717,  0.00143167,  0.14257721])]
file ' ダイナミックBT3_現行PIDq.csv ':  [array([1.24613217, 1.48612749, 0.37093761]), array([0.81071001, 0.86694998, 0.34461843])]
file ' ダイナミックBT_最適PIDq.csv ':  [array([1.06081142, 1.40165806, 0.36664543]), array([0.20376301, 0.09012261, 0.27468131])]
file ' ダイナミックBT3_最適PIDq.csv ':  [array([1.1219455 , 1.6033913 , 0.43628442]), array([ 0.16111302, -0.06525631,  0.21354077])]
file ' ダイナミックBT2_最適PIDq.csv ':  [array([0.94242762, 1.24807917, 0.39249896]), array([ 0.08582931, -0.11055557,  0.23209669])]
file ' ダイナミックBT_現行PIDq.csv ':  [array([2.07086402, 2.78693629, 1.26493491]), array([-0.66824745, -0.61671976, -0.25568081])]
file ' ダイナミックBT4_現行PIDq.csv ':  [array([1.65045816, 2.39830083, 0.42086623]), array([0.43746854, 0.52690855, 0.15455503])]
file ' ダイナミックBT_最適PID.csv ':  [array([1.29615924, 2.05212375, 0.20333408]), array([ 0.17110454,  0.24610951, -0.39111044])]
file 

array([[ 1.20934228e+00,  1.78605762e+00,  4.49159351e-01,
        -8.56171739e-02,  1.43167417e-03,  1.42577215e-01]])

[0.4491593506019006,
 0.3709376128376408,
 0.36664543346299655,
 0.4362844213994721,
 0.39249895559255205,
 1.2649349121953097,
 0.42086623125120387,
 0.2033340784458208,
 0.2033340784458208,
 0.21351930151366408,
 0.1902619057174998]